In [1]:
import numpy as np
import pandas as pd
import cv2
import pandas as pd 
import cv2
from glob import glob
import concurrent.futures
import numpy as np
import matplotlib.pyplot as plt

In [2]:
labels=pd.read_csv("Data/trainLabels.csv")
labels

image  level
0          10_left      0
1         10_right      0
2          13_left      0
3         13_right      0
4          15_left      1
...            ...    ...
35121  44347_right      0
35122   44348_left      0
35123  44348_right      0
35124   44349_left      0
35125  44349_right      1

[35126 rows x 2 columns]

In [3]:
enc_data = pd.get_dummies(labels['level'], prefix='level',dtype=int)
labels = pd.concat([labels, enc_data], axis=1)

In [4]:
labels.drop(columns=['level'],inplace=True)

In [5]:
labels.rename(columns={'level_0': 'No DR', 'level_1': 'Mild', 'level_2': 'Moderate','level_3': 'Severe','level_4': 'Proliferative DR'}, inplace=True)

In [6]:
labels.head()

image  No DR  Mild  Moderate  Severe  Proliferative DR
0   10_left      1     0         0       0                 0
1  10_right      1     0         0       0                 0
2   13_left      1     0         0       0                 0
3  13_right      1     0         0       0                 0
4   15_left      0     1         0       0                 0

In [13]:
labels.sum()

image               10_left10_right13_left13_right15_left15_right1...
No DR                                                           25810
Mild                                                             2443
Moderate                                                         5292
Severe                                                            873
Proliferative DR                                                  708
dtype: object

In [7]:
images_files = glob('Data/train/*')

In [8]:
def read_images(file_paths):
    results=[]
    for img_path in file_paths:
        img = cv2.imread(img_path)
        if img is not None:
            #Resizing the image
            resized_img = cv2.resize(img,(256,256))
            results.append([resized_img,img_path])

    return results

In [9]:
batch_size = 70
image_batches = [images_files[i:i + batch_size] for i in range(0, len(images_files), batch_size)]

In [10]:
with concurrent.futures.ThreadPoolExecutor(max_workers=8) as executor:  # Adjust max_workers as needed
    all_results = []
    for batch in image_batches:
        # Submit image processing tasks to the thread pool
        future = executor.submit(read_images, batch)
        all_results.append(future)

        # Collect and aggregate results
    images = []
    for future in concurrent.futures.as_completed(all_results):
        result = future.result()
        images.extend(result)


Premature end of JPEG file


In [14]:
cp=images
for img in cp:
    img[1]=img[1].replace("Data/train/", "").replace(".jpeg", "")

In [15]:
df=pd.DataFrame(cp,columns=['img_matrix','image'])

In [31]:
df.head()

img_matrix        image
0  [[[0, 0, 0], [0, 0, 0], [0, 0, 0], [0, 0, 0], ...    1763_left
1  [[[0, 0, 0], [0, 0, 0], [0, 0, 0], [0, 0, 0], ...  18113_right
2  [[[0, 0, 0], [0, 0, 0], [0, 0, 0], [0, 0, 0], ...    1887_left
3  [[[0, 0, 0], [1, 1, 1], [1, 1, 1], [1, 1, 1], ...   14060_left
4  [[[0, 0, 0], [0, 0, 0], [0, 0, 0], [0, 0, 0], ...   18880_left

In [17]:
final_df = pd.merge(df, labels, on='image')


In [28]:
cp_final=final_df.copy()


In [29]:
DEL_PADDING_RATIO = 0.02 
THRESHOLD_LOW = 7
THRESHOLD_HIGH = 180
MAX_TARGET_SIZE = (256, 256)

def del_black(img1):
    if img1.ndim == 2:
        img1 = np.expand_dims(img1, axis=-1)
    width, height = (img1.shape[1], img1.shape[0])

    (left, bottom) = (0, 0)
    (right, top) = (img1.shape[1], img1.shape[0])

    padding = int(min(width, height) * DEL_PADDING_RATIO)

    for i in range(width):
        array1 = img1[:, i, :]
        if np.sum(array1) > THRESHOLD_LOW * array1.shape[0] * array1.shape[1] and \
                np.sum(array1) < THRESHOLD_HIGH * array1.shape[0] * array1.shape[1]:
            left = i
            break
    left = max(0, left - padding)

    for i in range(width - 1, 0 - 1, -1):
        array1 = img1[:, i, :]
        if np.sum(array1) > THRESHOLD_LOW * array1.shape[0] * array1.shape[1] and \
                np.sum(array1) < THRESHOLD_HIGH * array1.shape[0] * array1.shape[1]:
            right = i
            break
    right = min(width, right + padding)

    for i in range(height):
        array1 = img1[i, :, :]
        if np.sum(array1) > THRESHOLD_LOW * array1.shape[0] * array1.shape[1] and \
                np.sum(array1) < THRESHOLD_HIGH * array1.shape[0] * array1.shape[1]:
            bottom = i
            break
    bottom = max(0, bottom - padding)

    for i in range(height - 1, 0 - 1, -1):
        array1 = img1[i, :, :]
        if np.sum(array1) > THRESHOLD_LOW * array1.shape[0] * array1.shape[1] and \
                np.sum(array1) < THRESHOLD_HIGH * array1.shape[0] * array1.shape[1]:
            top = i
            break
    top = min(height, top + padding)

    center_x = (left + right) // 2
    center_y = (bottom + top) // 2

    left = max(0, center_x - MAX_TARGET_SIZE[0] // 2)
    right = min(width, center_x + MAX_TARGET_SIZE[0] // 2)
    bottom = max(0, center_y - MAX_TARGET_SIZE[1] // 2)
    top = min(height, center_y + MAX_TARGET_SIZE[1] // 2)

    scale_factor = min(MAX_TARGET_SIZE[0] / (right - left), MAX_TARGET_SIZE[1] / (top - bottom))
    
    return cv2.resize(img1[bottom:top, left:right, :], None, fx=scale_factor, fy=scale_factor)

In [30]:
def preprocess_images(index):
    img=del_black(cp_final['img_matrix'][index])
    img=cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
    clahe = cv2.createCLAHE(clipLimit=5.0, tileGridSize=(8, 8))
    img=clahe.apply(img)
    img= cv2.GaussianBlur(img, (3,3), 0)
    cp_final['img_matrix'][index]=np.array(img)

In [31]:
for index in range(0,len(cp_final)):
    preprocess_images(index)  

/var/folders/sk/5p85qfdj4gs6687j53mbs7rw0000gn/T/ipykernel_11152/2331307931.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cp_final['img_matrix'][index]=np.array(img)
/var/folders/sk/5p85qfdj4gs6687j53mbs7rw0000gn/T/ipykernel_11152/2331307931.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cp_final['img_matrix'][index]=np.array(img)
/var/folders/sk/5p85qfdj4gs6687j53mbs7rw0000gn/T/ipykernel_11152/2331307931.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#

In [70]:
cv2.imshow('Original Image', final_df['img_matrix'][0])
cv2.imshow('Processed Image', cp_final['img_matrix'][0])

cv2.waitKey(27)
cv2.destroyAllWindows()

In [32]:
cp=cp_final.copy()
for index in range(len(cp) - 1, -1, -1): 
    if cp['img_matrix'].iloc[index].shape != (256,256):
        print("Dropping row with index:", index)
        cp = cp.drop(index)

# Reset the index after dropping rows
cp = cp.reset_index(drop=True)


Dropping row with index: 16627
Dropping row with index: 16527
Dropping row with index: 16248
Dropping row with index: 16243
Dropping row with index: 15822
Dropping row with index: 15083
Dropping row with index: 13686
Dropping row with index: 13511
Dropping row with index: 13145
Dropping row with index: 13089
Dropping row with index: 13065
Dropping row with index: 12388
Dropping row with index: 12251
Dropping row with index: 11926
Dropping row with index: 11750
Dropping row with index: 11653
Dropping row with index: 11299
Dropping row with index: 10704
Dropping row with index: 10439
Dropping row with index: 10400
Dropping row with index: 10350
Dropping row with index: 9687
Dropping row with index: 8276
Dropping row with index: 8202
Dropping row with index: 7512
Dropping row with index: 7493
Dropping row with index: 6758
Dropping row with index: 6289
Dropping row with index: 6269
Dropping row with index: 6076
Dropping row with index: 5814
Dropping row with index: 4817
Dropping row with i

In [34]:
for i in range(0,len(cp)):
    cv2.imwrite("Data/preprocessed/"+str(cp['image'][i])+".jpg",cp['img_matrix'][i])

In [35]:
labels_df=cp.drop(columns=['img_matrix'])

In [36]:
labels_df.to_csv("Data/labels_one_hot.csv",index=False)